# Colombia – Quality of Exports

In [146]:
import sys
sys.path.append("./modules")
import vistk
import pandas as pd
import json
import numpy as np

# Loading and processing metadata files
metadata = pd.read_json('sourceData/sitc_metadata_int_atlas.csv')
metadata.code = metadata.code.astype(int).astype(str).str.zfill(4)
data = pd.read_csv('sourceData/master_data.csv', 
                 usecols=["year", "iso3", "sitc4", "imports", "exports", "quality_imp", "quality_exp"]).sort(columns='year')
data.sitc4 = data.sitc4.astype(int).astype(str).str.zfill(4)
df = pd.merge(data, metadata, how='left', left_on='sitc4', right_on='code')
df['category'] = df['sitc4'].map(lambda x: str(x)[0])


df.head()

year iso3 sitc4  exports  quality_exp     imports  quality_imp  code  \
0  1984  DOM  0011      NaN          NaN    52.08442     0.702034  0011   
1  1984  JOR  7264      NaN          NaN   882.23070     1.248837  7264   
2  1984  MLT  7264  33.6984       1.1567   338.30020     0.937385  7264   
3  1984  BGD  7264      NaN          NaN  1146.31800     0.902277  7264   
4  1984  GHA  7264      NaN          NaN    31.46410     1.159864  7264   

     color  community_id              name category  
0  #ffe999            81      Live bovines        0  
1  #9edae5            10  Printing presses        7  
2  #9edae5            10  Printing presses        7  
3  #9edae5            10  Printing presses        7  
4  #9edae5            10  Printing presses        7

In [147]:
# Load countries dataset
with open('sourceData/countries.json') as data_file:    
    data = json.load(data_file)

# Flatten the countries dataset
from pandas.io.json import json_normalize
result = json_normalize(data)
df_countries = pd.DataFrame(result)

df = pd.merge(df, df_countries[['cca3', 'cca2', 'name.common', 'region', 'subregion']], how='left', left_on='iso3', right_on='cca3')
df = df.rename(columns = {'name.common':'country_name'})
df.head()

year iso3 sitc4  exports  quality_exp     imports  quality_imp  code  \
0  1984  DOM  0011      NaN          NaN    52.08442     0.702034  0011   
1  1984  JOR  7264      NaN          NaN   882.23070     1.248837  7264   
2  1984  MLT  7264  33.6984       1.1567   338.30020     0.937385  7264   
3  1984  BGD  7264      NaN          NaN  1146.31800     0.902277  7264   
4  1984  GHA  7264      NaN          NaN    31.46410     1.159864  7264   

     color  community_id              name category cca3 cca2  \
0  #ffe999            81      Live bovines        0  DOM   DO   
1  #9edae5            10  Printing presses        7  JOR   JO   
2  #9edae5            10  Printing presses        7  MLT   MT   
3  #9edae5            10  Printing presses        7  BGD   BD   
4  #9edae5            10  Printing presses        7  GHA   GH   

         country_name    region        subregion  
0  Dominican Republic  Americas        Caribbean  
1              Jordan      Asia     Western Asia  
2               Malta    Europe  Southern Europe  
3          Bangladesh      Asia    Southern Asia  
4               Ghana    Africa   Western Africa

In [148]:
# List of available regions
list(set(df['subregion']))

[nan,
 u'South-Eastern Asia',
 u'Middle Africa',
 u'Southern Europe',
 u'Micronesia',
 u'Western Africa',
 u'Central Asia',
 u'Caribbean',
 u'Eastern Africa',
 u'Northern Africa',
 u'Eastern Asia',
 u'Northern America',
 u'Polynesia',
 u'Southern Africa',
 u'Western Asia',
 u'Southern Asia',
 u'Melanesia',
 u'Australia and New Zealand',
 u'Eastern Europe',
 u'Northern Europe',
 u'Central America',
 u'South America',
 u'Western Europe']

# Line chart of Colombian products quality over time 

In [149]:
df_col = df[(df['iso3'] == 'COL')]
df_col.head()

year iso3 sitc4    exports  quality_exp   imports  quality_imp  code  \
86   1984  COL  7264        NaN          NaN  1062.921     1.393958  7264   
121  1984  COL  7267        NaN          NaN  7636.620     1.087847  7267   
213  1984  COL  7263   29.61946     1.029265  2405.174     1.001248  7263   
443  1984  COL  7269        NaN          NaN   733.707     2.740995  7269   
499  1984  COL  7271  843.11230     0.414522  1060.932     0.825406  7271   

       color  community_id                              name category cca3  \
86   #9edae5            10                  Printing presses        7  COL   
121  #9edae5            10           Other printing machines        7  COL   
213  #9edae5            10             Type-setting machines        7  COL   
443  #9edae5            10  Parts of printing press machines        7  COL   
499  #9edae5            10           Grain milling machinery        7  COL   

    cca2 country_name    region      subregion  
86    CO     Colombia  Americas  South America  
121   CO     Colombia  Americas  South America  
213   CO     Colombia  Americas  South America  
443   CO     Colombia  Americas  South America  
499   CO     Colombia  Americas  South America

In [150]:
df_col = df.groupby(['year'], as_index=False)['quality_exp'].mean()

In [151]:
df_col['iso3'] = "COL"

In [152]:
df_col.head()

year  quality_exp iso3
0  1984     1.286716  COL
1  1985     1.360835  COL
2  1986     5.405887  COL
3  1987     3.223797  COL
4  1988     1.286767  COL

# Evolution of national-level of quality of exports in Colombia (1962-2010)

In [144]:
linechart = vistk.Linechart(id='iso3', x='year', y='quality_exp', color='iso3', name='iso3',
                           group='iso3', y_invert=False, selection=['COL'])
linechart.draw(df_col)

<IPython.core.display.Javascript object>

# Evolution of 1-digit sector quality of exports in Colombia (1962-2010)

In [9]:
df_col_category_avg = df_col.groupby(['category', 'year'], as_index=False)['quality_exp'].mean()

In [10]:
linechart = vistk.Linechart(id='category', x='year', y='quality_exp', color='category', name='category',
                           group='category', y_invert=False, selection=["1","2","3","4","5","6","7","8","9","0"])
linechart.draw(df_col_category_avg)

<IPython.core.display.Javascript object>

# Evolution of national-level of quality of exports in Colombia in comparison to Latin America

In [41]:
df_sa = df[(df['subregion'].isin(['South America', 'Central America', 'Caribbean']))]

In [42]:
df_sa_avg = df_sa.groupby(['subregion','iso3', 'year'], as_index=False)['quality_exp'].mean()

In [186]:
# df_sa_avg['quality_exp'].notnull()
df_sa_avg['quality_exp'].fillna(df['imports'].mean())

0        True
1        True
2        True
3        True
4        True
5        True
6        True
7        True
8        True
9       False
10       True
11       True
12       True
13       True
14       True
15       True
16       True
17       True
18       True
19       True
20       True
21       True
22       True
23       True
24      False
25       True
26       True
27       True
28       True
29       True
        ...  
1057     True
1058     True
1059     True
1060     True
1061     True
1062     True
1063     True
1064     True
1065     True
1066     True
1067     True
1068     True
1069     True
1070     True
1071     True
1072     True
1073     True
1074     True
1075     True
1076     True
1077     True
1078     True
1079     True
1080     True
1081     True
1082     True
1083     True
1084     True
1085     True
1086     True
Name: quality_exp, dtype: bool

In [141]:
linechart = vistk.Linechart(id='iso3', x='year', y='quality_exp', color='subregion', name='iso3',
                           group='subregion', y_invert=False, selection=['COL'])
linechart.draw(df_sa_avg)

<IPython.core.display.Javascript object>

In [177]:
df_col_small = df[(df['iso3'] == 'COL')]
df_col_small = df_col_small[(df['sitc4'] == '7264')].drop_duplicates(cols='year')
df_col_small['imports'] = df_col_small['imports'].fillna(df['imports'].mean())

In [178]:
df_col_small

year iso3 sitc4     exports  quality_exp       imports  quality_imp  \
86       1984  COL  7264         NaN          NaN   1062.921000     1.393958   
99515    1985  COL  7264         NaN          NaN    742.633600     1.185201   
200112   1986  COL  7264    62.12165     0.573106   4351.108000     1.275809   
308134   1987  COL  7264   281.80330     0.691734   3669.457000     1.466445   
414105   1988  COL  7264    40.00871     0.326223   4634.611000     1.113140   
524231   1989  COL  7264         NaN          NaN   1782.339000     0.656049   
633933   1990  COL  7264         NaN          NaN   1465.589000     1.175106   
746778   1991  COL  7264   150.91540     0.473627  12557.500000     0.846160   
859414   1992  COL  7264   139.17010     0.233144  21945.200000     0.854425   
982291   1993  COL  7264         NaN          NaN  43682.240000     0.864921   
1106813  1994  COL  7264   713.90100     0.460957  44156.600000     1.002447   
1235111  1995  COL  7264         NaN          NaN  31095.640000     0.949597   
1367177  1996  COL  7264   188.39040     0.259327  20578.230000     0.949756   
1501380  1997  COL  7264         NaN          NaN   1926.518000     0.486591   
1633483  1998  COL  7264   708.95760     0.341565  21843.070000     0.862608   
1766531  1999  COL  7264    30.53765     1.774639   3352.629000     0.314551   
1905412  2000  COL  7264   101.14910    10.404170  60935.863452          NaN   
2035274  2001  COL  7264    50.34674     1.406178  60935.863452          NaN   
2163180  2002  COL  7264   969.16000     0.645633  23116.060000     0.869139   
2293839  2003  COL  7264   510.76970     0.612872  25428.380000     0.852289   
2422794  2004  COL  7264   519.80300     0.663894  56939.640000     1.124614   
2558679  2005  COL  7264   759.55420     0.602556  29567.000000     1.016768   
2674202  2006  COL  7264  1347.41900     0.693811  38806.480000     0.892429   
2781745  2007  COL  7264  1325.94700     0.833924  62660.770000     0.944535   
2906692  2008  COL  7264   309.02800     0.932805  18463.580000     1.092809   
3038727  2009  COL  7264         NaN          NaN  10445.090000     1.446844   
3168755  2010  COL  7264   108.80110     4.621132  14007.710000     1.869713   
3298956  2011  COL  7264   261.20000     1.002853  21533.340000     0.761282   

         code    color  community_id              name category cca3 cca2  \
86       7264  #9edae5            10  Printing presses        7  COL   CO   
99515    7264  #9edae5            10  Printing presses        7  COL   CO   
200112   7264  #9edae5            10  Printing presses        7  COL   CO   
308134   7264  #9edae5            10  Printing presses        7  COL   CO   
414105   7264  #9edae5            10  Printing presses        7  COL   CO   
524231   7264  #9edae5            10  Printing presses        7  COL   CO   
633933   7264  #9edae5            10  Printing presses        7  COL   CO   
746778   7264  #9edae5            10  Printing presses        7  COL   CO   
859414   7264  #9edae5            10  Printing presses        7  COL   CO   
982291   7264  #9edae5            10  Printing presses        7  COL   CO   
1106813  7264  #9edae5            10  Printing presses        7  COL   CO   
1235111  7264  #9edae5            10  Printing presses        7  COL   CO   
1367177  7264  #9edae5            10  Printing presses        7  COL   CO   
1501380  7264  #9edae5            10  Printing presses        7  COL   CO   
1633483  7264  #9edae5            10  Printing presses        7  COL   CO   
1766531  7264  #9edae5            10  Printing presses        7  COL   CO   
1905412  7264  #9edae5            10  Printing presses        7  COL   CO   
2035274  7264  #9edae5            10  Printing presses        7  COL   CO   
2163180  7264  #9edae5            10  Printing presses        7  COL   CO   
2293839  7264  #9edae5            10  Printing presses        7  COL   CO   
2422794  7264  #9edae5            10  Printing presses        7  COL   

In [179]:
caterplotTime = vistk.CaterplotTime(id='iso3', color='iso3', name='iso3', x='year', 
                            y='imports', group='iso3')
caterplotTime.draw(df_col_small)

<IPython.core.display.Javascript object>

In [ ]:
caterplotTime = vistk.CaterplotTime(id='iso3', color='subregion', name='iso3', x='year', 
                            y='quality_exp', r='quality_exp', group='subregion')
caterplotTime.draw(df_sa)

# Distribution of product-level quality of exports by 1-digit sector in Colombia (2010), highlighting key “garment” products

In [31]:
caterplot = vistk.Caterplot(id='sitc4', color='color', name='sitc4', x='year', 
                            y='quality_exp', r='exports', year=2010, group='category', selection=["7283", "8310", "2873"])
caterplot.draw(df_col)

<IPython.core.display.Javascript object>

In [18]:
with open('/Users/rvuillemot/Dev/vis-toolkit-datasets/data/quality_%s_%s.json' % (country, year), 'w') as fp:
    fp.write(df_caterplot.to_json(orient='records'))

### Top-10 Products Quality in Colombia in 2010

In [64]:
# Generate a pretty table
from ipy_table import *
import numpy as np

df_table = df_col[(df_col['year'] == 2010)].head(10).reset_index(drop=True).reset_index()
df_table = df_table[['sitc4', 'name', 'quality_exp']]
df_table['rank'] = df_table['quality_exp'].rank(ascending=False, method='first')

df_table['quality_exp'] = df_table['quality_exp'].dropna()

# df_table['rank'] = df_table['rank'].apply(lambda x: int(x))

df_table.sort(['quality_exp'], ascending=False)


table = df_table.as_matrix()

header = np.asarray(df_table.columns)
header[0] = 'Code'
#header[0] = 'Description'
# df.rename(columns=lambda x: x[1:], inplace=True)
table_with_header = np.concatenate(([header], table))

# Basic themes
# Detais http://nbviewer.ipython.org/github/epmoyer/ipy_table/blob/master/ipy_table-Introduction.ipynb
make_table(table_with_header)
apply_theme('basic')
# Only show the top-10
set_row_style(1, color='yellow')

# Full list of "key" sectors

TBD